In [1]:
import pandas as pd
import numpy as np
#!pip install -U ydata-profiling

**injection de donnée**


1.   ajouter des dropoff_datetime antérieur à pickup_datetime (5%)
2.   Mettre certaine date dans le future (en années)
3.   Mettre des Nan (avec la methode MCAR) (5%)
4.   Repeter quelques (pickup_latitude	pickup_longitude) comme (dropoff_latitude	dropoff_longitude)

5.   Injecter des valeurs extremes dans fare_amount (exemple 200,300)
6.   Annuler certaines fare_amount
7.   Remplacer certaines ligne ou on a Credit Card par Credi Card
8.   Ajouter des longitudes et latitudes hors de new york sur pickup et dropoff
9.   Ajouter des dévises multiples




In [3]:
df = pd.read_csv('NYC_Taxi_dataset.csv')
df.head(2)

pickup_datetime     dropoff_datetime  pickup_latitude  \
0  2023-02-20 17:27:00  2023-02-20 17:49:00        40.808941   
1  2023-02-28 19:41:00  2023-02-28 20:07:00        40.685842   

   pickup_longitude  dropoff_latitude  dropoff_longitude  trip_distance_miles  \
0        -73.914482         40.807336         -73.905270                 1.03   
1        -73.855449         40.663358         -73.826745                 4.02   

   fare_amount  passenger_count payment_type  
0         5.84                5  Credit Card  
1        20.88                4      Unknown

In [ ]:
df.shape

(800, 10)

In [ ]:
df.dtypes

pickup_datetime         object
dropoff_datetime        object
pickup_latitude        float64
pickup_longitude       float64
dropoff_latitude       float64
dropoff_longitude      float64
trip_distance_miles    float64
fare_amount            float64
passenger_count          int64
payment_type            object
dtype: object

In [ ]:
df['payment_type'].unique()

array(['Credit Card', 'Unknown', 'Cash', 'Dispute', 'No Charge'],
      dtype=object)

In [ ]:
print(f"dataframe shape : {df.shape}")
print(f"dataframe describe \n: {df.describe()}")

dataframe shape : (800, 10)
dataframe describe 
:        pickup_latitude  pickup_longitude  dropoff_latitude  dropoff_longitude  \
count       800.000000        800.000000        800.000000         800.000000   
mean         40.751655        -73.878843         40.751367         -73.878629   
std           0.085945          0.104064          0.087704           0.105873   
min          40.600025        -74.049958         40.571280         -74.075956   
25%          40.679936        -73.972376         40.679864         -73.970998   
50%          40.750586        -73.880704         40.752038         -73.884815   
75%          40.825291        -73.791455         40.824134         -73.788010   
max          40.899676        -73.700125         40.924537         -73.678499   

       trip_distance_miles  fare_amount  passenger_count  
count           800.000000   800.000000       800.000000  
mean              2.558612    12.636225         3.016250  
std               0.931247     3.352882    

In [ ]:
df.isna().sum()

pickup_datetime        0
dropoff_datetime       0
pickup_latitude        0
pickup_longitude       0
dropoff_latitude       0
dropoff_longitude      0
trip_distance_miles    0
fare_amount            0
passenger_count        0
payment_type           0
dtype: int64

In [ ]:
len(df)

800

## Emettre les conversions des mesures

In [ ]:
rng=np.random.default_rng(42)
currency=["$","€","¥","£"]

for i in range(len(df)):
  n=rng.choice(currency)
  if n=="$":
    df.loc[i,"fare_amount"]=str(round(float(df.loc[i,"fare_amount"]),2))+n
  elif n=="€":
    df.loc[i,"fare_amount"]=str(round(float(df.loc[i,"fare_amount"]*0.85),2))+n
  elif n=="¥":
    df.loc[i,"fare_amount"]=str(round(float(df.loc[i,"fare_amount"]*155.067),2))+n
  elif n=="£":
    df.loc[i,"fare_amount"]=str(round(float(df.loc[i,"fare_amount"]*0.747),2))+n




/tmp/ipython-input-2203412451.py:7: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '5.84$' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.loc[i,"fare_amount"]=str(round(float(df.loc[i,"fare_amount"]),2))+n


In [ ]:
df["fare_amount"].head(10)

0       5.84$
1       15.6£
2    2192.65¥
3       9.38€
4       13.7€
5      10.08£
6       10.6$
7    2712.12¥
8      13.06$
9      10.19$
Name: fare_amount, dtype: object

## On transforme les dates en format datetime pour pouvoir opérer sur ces dernières

In [ ]:
df['pickup_datetime']  = pd.to_datetime(df['pickup_datetime'])
df['dropoff_datetime'] = pd.to_datetime(df['dropoff_datetime'])

## On actualise dropoff_datetime pour qu'il corresponde a pickup_datetime - une valeur dépendant du pourcentage d'erreur ce qui assure qu'on a bien dropoff_datetime < pickup_datetime  5% d'erreur

In [ ]:
rng = np.random.default_rng(42)

n_rows = len(df)
error_rate = 0.05

row_indices = np.arange(n_rows)
n_error_rows = int(error_rate * n_rows)

error_rows_idx = rng.choice(row_indices, size=n_error_rows, replace=False)

# on force dropoff_datetime < pickup_datetime
df.loc[error_rows_idx, 'dropoff_datetime'] = df.loc[error_rows_idx, 'pickup_datetime'] - pd.to_timedelta(
    rng.integers(1, 60, size=n_error_rows), unit='m'
)


In [ ]:
df[df['pickup_datetime']>df['dropoff_datetime']]

pickup_datetime    dropoff_datetime  pickup_latitude  \
50  2023-02-07 07:05:00 2023-02-07 06:15:00        40.636189   
65  2023-01-13 18:52:00 2023-01-13 18:37:00        40.624958   
67  2023-02-02 10:38:00 2023-02-02 10:12:00        40.673100   
72  2023-02-07 22:52:00 2023-02-07 21:56:00        40.788175   
73  2023-02-07 02:17:00 2023-02-07 02:11:00        40.817025   
99  2023-02-04 11:03:00 2023-02-04 10:10:00        40.703037   
142 2023-01-14 06:23:00 2023-01-14 05:55:00        40.878275   
154 2023-02-03 01:24:00 2023-02-03 01:14:00        40.799578   
179 2023-02-08 21:55:00 2023-02-08 21:37:00        40.727292   
221 2023-01-08 12:08:00 2023-01-08 11:21:00        40.896710   
289 2023-01-31 08:15:00 2023-01-31 07:58:00        40.887553   
316 2023-02-21 01:09:00 2023-02-21 01:06:00        40.776248   
331 2023-02-12 14:55:00 2023-02-12 14:32:00        40.871268   
335 2023-01-29 22:28:00 2023-01-29 22:16:00        40.704870   
350 2023-02-24 10:00:00 2023-02-24 09:51:00        40.812887   
351 2023-02-07 11:21:00 2023-02-07 10:33:00        40.887804   
356 2023-01-16 17:12:00 2023-01-16 16:53:00        40.643579   
390 2023-02-22 12:58:00 2023-02-22 12:17:00        40.626222   
398 2023-02-08 07:42:00 2023-02-08 06:52:00        40.665411   
405 2023-01-25 20:05:00 2023-01-25 19:18:00        40.613025   
430 2023-01-23 02:03:00 2023-01-23 01:13:00        40.677204   
440 2023-01-13 14:32:00 2023-01-13 14:04:00        40.727055   
499 2023-03-01 20:06:00 2023-03-01 19:36:00        40.823385   
505 2023-01-23 03:09:00 2023-01-23 02:54:00        40.748952   
506 2023-01-03 12:42:00 2023-01-03 11:52:00        40.727829   
535 2023-01-22 10:59:00 2023-01-22 10:13:00        40.713511   
556 2023-01-11 11:41:00 2023-01-11 11:32:00        40.650244   
568 2023-02-25 09:17:00 2023-02-25 08:30:00        40.838681   
589 2023-02-24 14:56:00 2023-02-24 14:55:00        40.672889   
609 2023-01-07 21:17:00 2023-01-07 20:44:00        40.631165   
613 2023-01-10 01:30:00 2023-01-10 00:48:00        40.890231   
648 2023-01-31 13:26:00 2023-01-31 12:46:00        40.736197   
654 2023-02-13 13:13:00 2023-02-13 12:35:00        40.842588   
657 2023-01-26 08:06:00 2023-01-26 07:26:00        40.796665   
660 2023-03-01 10:50:00 2023-03-01 10:02:00        40.649001   
684 2023-01-22 12:20:00 2023-01-22 11:32:00        40.679298   
705 2023-01-27 19:42:00 2023-01-27 19:16:00        40.619182   
726 2023-01-02 19:55:00 2023-01-02 19:17:00        40.688355   
753 2023-02-24 17:29:00 2023-02-24 16:47:00        40.797298   
773 2023-01-13 20:56:00 2023-01-13 20:22:00        40.855546   

     pickup_longitude  dropoff_latitude  dropoff_longitude  \
50         -73.912303         40.618425         -73.908300   
65         -73.814556         40.602105         -73.814219   
67         -74.014389         40.675546         -74.007868   
72         -73.882554         40.797270         -73.890961   
73         -73.968347         40.827687         -73.997667   
99         -74.028741         40.711437         -74.005058   
142        -73.785917         40.897728         -73.794331   
154        -73.702098         40.770605         -73.678499   
179        -73.760714         40.715231         -73.755449   
221        -73.749380         40.879806         -73.766847   
289        -73.849200         40.874974         -73.836294   
316        -73.781526         40.772104         -73.775500   
331        -73.915064         40.900622         -73.916666   
335        -73.908274         40.728997         -73.898751   
350        -73.835795         40.819527         -73.808732   
351        -73.993276         40.863363         -73.986253   
356        -74.018197         40.649626         -74.025070   
390        -73.801465         40.639157         -73.811167   
398        -73.701764         40.678720         -73.694329   
405        -73.969667         40.629721         -73.960238   
430        -73.786122         40.681256         -73.812036   
440        -73.7545

## On crée des valeurs extrême de pickup_datetime et dropoff_datetime

In [ ]:
years_offset = rng.integers(3, 10, size=n_error_rows)
available_indices = np.setdiff1d(df.index, error_rows_idx)
err_idx=rng.choice(available_indices, size=n_error_rows, replace=False)


df.loc[error_rows_idx, 'pickup_datetime'] = (
    df.loc[err_idx, 'pickup_datetime']
    + pd.to_timedelta(365 * years_offset, unit='D')
)

df.loc[error_rows_idx, 'dropoff_datetime'] = (
    df.loc[error_rows_idx, 'dropoff_datetime']
    + pd.to_timedelta(365 * years_offset, unit='D')
)


## On duplique les valeurs, en les ajoutant dans le dataFrame 3% d'erreur

De ce que j'ai vu, il est recommandé de garder ce modèle là au lieu d'écraser la donnée

In [ ]:
rng = np.random.default_rng(42)

duplicate_rate = 0.03  # 3 %
n_rows = len(df)

row_indices = np.arange(n_rows)
n_duplicate_rows = int(duplicate_rate * n_rows)

# indices des lignes à dupliquer (triés pour garder l'ordre)
duplicate_src_idx = np.sort(
    rng.choice(row_indices, size=n_duplicate_rows, replace=False)
)

# on stocke les lignes dans une liste en dupliquant localement
rows_list = []
dup_set = set(duplicate_src_idx)

for i in range(n_rows):
    # ligne originale
    rows_list.append(df.iloc[i])

    # si cette ligne doit être dupliquée, on ajoute un doublon juste après
    if i in dup_set:
        rows_list.append(df.iloc[i].copy())

# on recrée le DataFrame avec les doublons insérés localement
df = pd.DataFrame(rows_list).reset_index(drop=True)


In [ ]:
df.tail(5)

pickup_datetime    dropoff_datetime  pickup_latitude  \
819 2023-01-20 11:23:00 2023-01-20 11:38:00        40.630064   
820 2023-01-10 09:47:00 2023-01-10 10:19:00        40.763429   
821 2023-03-01 14:20:00 2023-03-01 14:22:00        40.704108   
822 2023-02-15 09:59:00 2023-02-15 10:40:00        40.717329   
823 2023-01-02 14:03:00 2023-01-02 14:41:00        40.693153   

     pickup_longitude  dropoff_latitude  dropoff_longitude  \
819        -73.816604         40.616475         -73.810151   
820        -73.886102         40.735097         -73.860627   
821        -74.006618         40.679671         -73.985324   
822        -73.860626         40.695675         -73.846361   
823        -73.828832         40.703059         -73.806419   

     trip_distance_miles fare_amount  passenger_count payment_type  
819                 1.66       6.75€                4  Credit Card  
820                 4.20       13.3£                4         Cash  
821                 3.57      13.57€                2  Credit Card  
822                 2.86      13.52€                1  Credit Card  
823                 2.70       9.88€                1         Cash

In [ ]:
len(df)

824

## Ajout des NAN selon le modèle MCAR

In [ ]:
cols_mcar = ['trip_distance_miles', 'fare_amount', 'passenger_count']

for col in cols_mcar:
    n_missing_rows = int(error_rate * n_rows)
    missing_rows_idx = rng.choice(row_indices, size=n_missing_rows, replace=False)
    df.loc[missing_rows_idx, col] = np.nan

In [ ]:
df.isna().sum()

pickup_datetime        42
dropoff_datetime        0
pickup_latitude         0
pickup_longitude        0
dropoff_latitude        0
dropoff_longitude       0
trip_distance_miles    40
fare_amount            40
passenger_count        40
payment_type            0
dtype: int64

 ## Injecter des valeurs extrêmes dans fare_amount

In [ ]:
n_extreme = int(0.02 * len(df)) # 2% de valeurs extrême
extreme_values = range(200, 300)
indices = np.random.choice(df.index, n_extreme, replace=False)

In [ ]:
df.loc[indices,'fare_amount'] =  np.random.choice(extreme_values,n_extreme)

## Annuler certaines fare_amount

In [ ]:
n_to_annulate = int(0.03 * len(df)) # 3% des valeurs à NAn
available_indices = np.setdiff1d(df.index, indices)
indices_to_annulate = np.random.choice(available_indices, n_to_annulate, replace=False)
df.loc[indices_to_annulate,'fare_amount'] = 0

In [ ]:
df.loc[:,'fare_amount'].head(30)

0        5.84$
1        15.6£
2     2192.65¥
3            0
4        13.7€
5       10.08£
6        10.6$
7     2712.12¥
8       13.06$
9       10.19$
10    1905.77¥
11        6.7£
12     2769.5¥
13      11.08£
14    2834.62¥
15       8.64£
16    2017.42¥
17      14.33$
18       9.64£
19       7.43€
20    2236.07¥
21      10.91€
22      12.16$
23         NaN
24       5.36£
25    1786.37¥
26       9.81€
27         NaN
28    2896.65¥
29      12.75€
Name: fare_amount, dtype: object

## Remplacer certaines ligne ou on a Credit Card par ["credit card", "CREDIT CARD", " CREDIT CARD "], 'Cash' par 'cash', et 'Dispute' par ['Conflict', 'Disagreement', 'Issue']

In [ ]:
n_anomaly = int(0.05 * len(df)) # 5%
eligible_indices = df.index[df['payment_type'].isin(['Credit Card', 'Cash', 'Dispute'])]
anomaly_indices = np.random.choice(eligible_indices, n_anomaly, replace=False)

for idx in anomaly_indices:
    val = df.loc[idx, 'payment_type']
    if val == 'Credit Card':

        df.loc[idx, 'payment_type'] = np.random.choice(['credit card', 'CREDIT CARD', ' CREDIT CARD '])
    elif val == 'Cash':
        df.loc[idx, 'payment_type'] = 'cash'
    elif val == 'Dispute':

        df.loc[idx, 'payment_type'] = np.random.choice(['Conflict', 'Disagreement', 'Issue'])

In [ ]:
df['payment_type'].value_counts()

payment_type
Credit Card      513
Cash             191
Unknown           36
No Charge         26
Dispute           17
CREDIT CARD       13
cash               9
credit card        9
 CREDIT CARD       9
Disagreement       1
Name: count, dtype: int64

## Ajouter des longitudes et latitudes hors de new york sur pickup et dropoff

Limite coordonnées approximatif de new york
https://gist.github.com/ix4/6f44e559b29a72c4c5d130ac13aad317?short_path=467dc07

```
nyc_bounds = {
    'min_lon': -74.25559,
    'max_lon': -73.70001,
    'min_lat': 40.49612,
    'max_lat': 40.91553
}
```

In [ ]:
n_outside = int(0.05 * len(df))  # 5% des lignes
indices_out = np.random.choice(df.index, n_outside, replace=False)
df.loc[indices_out, 'pickup_longitude'] = np.random.uniform(-125, -70, n_outside)
df.loc[indices_out, 'pickup_latitude']  = np.random.uniform(25, 50, n_outside)
df.loc[indices_out, 'dropoff_longitude'] = np.random.uniform(-125, -70, n_outside)
df.loc[indices_out, 'dropoff_latitude']  = np.random.uniform(25, 50, n_outside)


In [ ]:
df.to_csv("/content/NYC_Taxi_dataset_with_anomalies.csv")

In [ ]:
from ydata_profiling import ProfileReport
profile = ProfileReport(df, title="Profiling Report")


In [ ]:
df2=pd.read_csv("/content/NYC_Taxi_dataset_with_anomalies.csv")

In [ ]:
df2

Unnamed: 0      pickup_datetime     dropoff_datetime  pickup_latitude  \
0             0  2023-02-20 17:27:00  2023-02-20 17:49:00        40.808941   
1             1  2023-02-28 19:41:00  2023-02-28 20:07:00        40.685842   
2             2  2023-02-14 08:37:00  2023-02-14 09:07:00        40.668055   
3             3  2023-01-16 23:54:00  2023-01-17 00:40:00        40.765394   
4             4  2023-02-11 01:16:00  2023-02-11 01:35:00        40.815841   
..          ...                  ...                  ...              ...   
819         819  2023-01-20 11:23:00  2023-01-20 11:38:00        40.630064   
820         820  2023-01-10 09:47:00  2023-01-10 10:19:00        40.763429   
821         821  2023-03-01 14:20:00  2023-03-01 14:22:00        40.704108   
822         822  2023-02-15 09:59:00  2023-02-15 10:40:00        40.717329   
823         823  2023-01-02 14:03:00  2023-01-02 14:41:00        40.693153   

     pickup_longitude  dropoff_latitude  dropoff_longitude  \
0          -73.914482         40.807336         -73.905270   
1          -73.855449         40.663358         -73.826745   
2          -74.045050         40.642572         -74.055617   
3          -73.753324         40.775285         -73.775441   
4          -73.727328         40.836115         -73.746976   
..                ...               ...                ...   
819        -73.816604         40.616475         -73.810151   
820        -73.886102         40.735097         -73.860627   
821        -74.006618         40.679671         -73.985324   
822        -73.860626         40.695675         -73.846361   
823        -73.828832         40.703059         -73.806419   

     trip_distance_miles fare_amount  passenger_count payment_type  
0                   1.03       5.84$              5.0  Credit Card  
1                   4.02       15.6£              4.0      Unknown  
2                   3.04    2192.65¥              5.0  Credit Card  
3                   2.67           0              4.0  Credit Card  
4                   3.11       13.7€              3.0  Credit Card  
..                   ...         ...              ...          ...  
819                 1.66       6.75€              4.0  Credit Card  
820                 4.20       13.3£              4.0         Cash  
821                 3.57      13.57€              2.0  Credit Card  
822                 2.86      13.52€              1.0  Credit Card  
823                 2.70       9.88€              1.0         Cash  

[824 rows x 11 columns]

In [ ]:
from ydata_profiling import ProfileReport
profile = ProfileReport(df, title="Profiling Report")

In [ ]:
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 10/10 [00:00<00:00, 41.09it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]